<a href="https://colab.research.google.com/github/guscldns/Focus-Read/blob/main/Dount/json_to_text%2C_image.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

## 데이터 및 라이브러리 import

In [ ]:
# # 샘플파일
# !gdown 1rswWV67Idv8OXI1qQ7o5aSSWvP_uA5MW
# 맑음고딕 폰트
!gdown 1G4jAcJLy_1PC9YQR36t7jMapj9da4vPd

In [ ]:
# cuda 사용하도록 변경
import torch
print ( "CUDA 사용 가능:" , torch.cuda.is_available())
!nvcc --version

# 관련 라이브러리, 파일 설치
!git clone https://github.com/clovaai/donut.git
!cd donut && pip install

In [ ]:
!pip install gradio
!pip install timm==0.4.9
!pip install Transformers==4.25.1

In [ ]:
# 라이브러리
import zipfile
import os
import json
import torch
import argparse
import gradio as gr
from donut import DonutModel
from PIL import Image, ImageDraw, ImageFont
torch.cuda.is_available()

## 데이터 변환 : synthdog 사용

In [ ]:
# donut/synthdog 설치용
!pip install synthtiger

In [ ]:
import os
import json

foilderlist = os.listdir('./sample')

# 'kowiki.text' 파일 내용 초기화
with open(f'./donut/synthdog/resources/corpus/kowiki.txt', "w", encoding='utf-8') as fi:
    fi.truncate(0)
fi.close()

for i in foilderlist:
    per_path = f'./sample/{i}/20per'
    sent_path = f'./sample/{i}/2~3sent'
    per_list = os.listdir(per_path)
    sent_list = os.listdir(sent_path)

    # 원문만 불러오기
    for a, j in enumerate(per_list):
        with open(f'{per_path}/{j}', 'r', encoding='utf-8') as file:
            text = json.load(file)
            ground_truth_parse =  f" {text['Meta(Refine)']['passage']}"
            paasage = ground_truth_parse.replace('\n', ' ')

            # 원문 'kowiki.text' 에 덮어쓰기
            with open(f'./donut/synthdog/resources/corpus/kowiki.txt', 'a', encoding='utf-8') as f:
                f.write(f'{paasage} \n')

In [ ]:
%cd ./donut/synthdog
# 환경 변수 설정
!export OBJC_DISABLE_INITIALIZE_FORK_SAFETY=YES

# SynthDoG 실행
!synthtiger -o /home/alpaco/final_Project/donut/synthdog/outputs/KoreanData -c 100 -w 8 -v /home/alpaco/final_Project/donut/synthdog/template.py SynthDoG /home/alpaco/final_Project/donut/synthdog/config_ko.yaml

## dount

### 훈련

In [ ]:
# model = DonutModel.from_pretrained("naver-clova-ix/donut-base-finetuned-cord-v2")
## 모델 학습
# 만든 데이터 경로 train_cord.yaml에서 변경
# (예시) dataset_name_or_paths: [./donut/synthdog/outputs/KoreanData]
# cuda 사용하도록 변경
import torch
    # --resume_from_checkpoint_path "/home/alpaco/final_Project/donut/result/train_cord/20230904_113810/" \
!nvcc --version

!CUDA_VISIBLE_DEVICES=1 python /home/alpaco/final_Project/donut/train.py --config /home/alpaco/final_Project/donut/config/train_cord.yaml \
    --pretrained_model_name_or_path "naver-clova-ix/donut-base-finetuned-cord-v2" \
    --dataset_name_or_paths '["/home/alpaco/final_Project/donut/synthdog/outputs/KoreanData"]'\
    --resume_from_checkpoint_path "/home/alpaco/final_Project/donut/result/train_cord/test01/" \
    --result_path "/home/alpaco/final_Project/donut/result/" \
    --exp_version "test01"

nvcc: NVIDIA (R) Cuda compiler driver
Copyright (c) 2005-2022 NVIDIA Corporation
Built on Wed_Sep_21_10:33:58_PDT_2022
Cuda compilation tools, release 11.8, V11.8.89
Build cuda_11.8.r11.8/compiler.31833905_0


resume_from_checkpoint_path: /home/alpaco/final_Project/donut/result/train_cord/test01/
result_path: /home/alpaco/final_Project/donut/result/
pretrained_model_name_or_path: naver-clova-ix/donut-base-finetuned-cord-v2
dataset_name_or_paths: 
  - /home/alpaco/final_Project/donut/synthdog/outputs/KoreanData
sort_json_key: False
train_batch_sizes: 
  - 3
val_batch_sizes: 
  - 1
input_size: 
  - 1280
  - 960
max_length: 768
align_long_axis: False
num_nodes: 1
seed: 2022
lr: 3e-05
warmup_steps: 15000
num_training_samples_per_epoch: 800
max_epochs: 1100
max_steps: -1
num_workers: 8
val_check_interval: 1.0
check_val_every_n_epoch: 5
gradient_clip_val: 1.0
verbose: True
exp_name: train_cord
exp_version: test01
Config is saved at /home/alpaco/final_Project/donut/result/train_cord/test01/config.yaml
Global seed set to 2022
/home/alpaco/anaconda3/envs/mento/lib/python3.11/site-packages/torch/functional.py:504: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the ind

### 테스트 파일로 성능 확인

In [ ]:
# test
!CUDA_VISIBLE_DEVICES=1 python /home/alpaco/final_Project/donut/test.py --dataset_name_or_path /home/alpaco/final_Project/donut/synthdog/outputs/KoreanData --pretrained_model_name_or_path /home/alpaco/final_Project/donut/result/train_cord/test01 --save_path /home/alpaco/final_Project/donut/result/output.json

/home/alpaco/anaconda3/envs/mento/lib/python3.11/site-packages/torch/functional.py:504: UserWarning: torch.meshgrid: in an upcoming release, it will be required to pass the indexing argument. (Triggered internally at ../aten/src/ATen/native/TensorShape.cpp:3483.)
  return _VF.meshgrid(tensors, **kwargs)  # type: ignore[attr-defined]
100%|███████████████████████████████████████| 1103/1103 [28:42<00:00,  1.56s/it]
Total number of samples: 1103, Tree Edit Distance (TED) based accuracy score: 0.6357350140578183, F1 accuracy score: 0.04623753399818677


## 실제 데이터로 테스트

In [ ]:
from donut import DonutModel
import torch
from PIL import Image


pretrained_model = DonutModel.from_pretrained("/home/alpaco/final_Project/donut/result/train_cord/test01")
if torch.cuda.is_available():
    pretrained_model.half()
    device = torch.device("cuda")
    pretrained_model.to(device)
else:
    pretrained_model.encoder.to(torch.bfloat16)
pretrained_model.eval()

task_name = "synthdog"
task_prompt = f"<s_{task_name}>"

input_img = Image.open("/home/alpaco/final_Project/donut/20230906_110217.jpg")
output = pretrained_model.inference(image=input_img, prompt=task_prompt)["predictions"][0]
print(output)

{'text_sequence': "체험 보았을 때 브라이언은 깨달는다. 언제가 신문에서 젊은 창업, 어떻게 눈치를 주 수가 회사를 창업해 개인용 컴퓨터를 만드는데, 앞으로 기대가 크 립니다. 그렇게 터격 는 내용을 읽었던 게 머리에 띠오른다. '갓! 이 사람이 스티브 잡스구나' 코로별 CBO로 신격화되기 30년 전꿉이지만 그 당시에도 신문 퀴중으로 날아가면(生)이 마지막이구나 왔는지 눈치챈다. 브라이언이 흑린 PB에 종이가 젖어가고. 스티브 커를 마음으로 몬터 는 이제 점점 화가 나는지 재촉하기 시작한다. “지난번에 이보다 더 많은 짐을 신고 간 적이 있다고요. 이제 그만 갑시다.” 쉬 출력을 최대로 높 아속한 교장은 아무 말도 없이 브라이언에게 결정하라고 눈짓 을 보여주기라도 하나 을 준다. 전자장비 계산 중량. 그날의 온도, 파일럿을 포함한 세 명 의 건장한 남자들의 중량을 계산하자. 브라이언의 눈에는 이룩이 쳐다. 거의 활주로 구 아슬아슬해 보인다. 안전하게 이룩하기에는 활주로가 너무 왔다. 1천천히 남아오른다 브라이언은 잠시 망설이더니 스티브에게 어렵게 말을 씻낸다. ”이 모든 중량을 감당하기엔 여기 활주로가 너무  풀습니다. 제 가 여기서 15분 거리에 있는 몬테베이 공항으로 비행기를 물고 가 졌습니다. 두 분은 차로 이동해 거기서 밥승하십시오. 그러면 기름 산호세 공항으로 오 중량도 조금 줄고, 몬테베이 공항 활주로는 여기보다 세 배나 길 낄 건물 앞에 비행 기 때문에 우리 모두 타고 이룩하는 데 문제가 없습니다.” 하며알으낄 스티브. 2 0 0 0"}
